In [1]:
import pandas as pd
import networkx as nx
import matplotlib.pyplot as plt
from math import sin, cos, sqrt, atan2, radians

In [2]:
def calculate_time_difference(time1: str, time2: str) -> int:
    def convert_str_time_to_int(time: str) -> int:
        splitted_time = time.split(':')
        return int(splitted_time[2]) + int(splitted_time[1]) * 60 + int(splitted_time[0]) * 3600
    return convert_str_time_to_int(time= time2) - convert_str_time_to_int(time= time1) + 5

In [3]:
def extract_coordinates(raw_lat, raw_lon):
    lat = round(float(raw_lat),6)
    lon = round(float(raw_lon),6)
    return (lon,lat)

In [4]:
def calculate_distance_between_coordinates_in_meters(lat1: float, lon1: float, lat2: float, lon2: float):
    R = 6373.0
    dlat = radians(lat2 - lat1)
    dlon = radians(lon2 - lon1)
    a = (sin(dlat / 2) * sin(dlat / 2) +
         cos(radians(lat1)) * cos(radians(lat2)) *
         sin(dlon / 2) * sin(dlon / 2))
    c = 2 * atan2(sqrt(a), sqrt(1 - a))
    d = R * c
    return d * 1000

In [5]:
stops = pd.read_csv('stops.txt', low_memory=False)
#pathways = pd.read_csv('pathways.txt', low_memory=False)
routes = pd.read_csv('routes.txt', low_memory=False)
trips = pd.read_csv('trips.txt', low_memory=False)
#shapes = pd.read_csv('shapes.txt', low_memory=False)
stop_times = pd.read_csv('stop_times.txt', low_memory=False)

In [6]:
#Remove unnecessary columns
stops = stops[['stop_id','stop_name','stop_lat','stop_lon']]
trips = trips[['route_id','trip_id','direction_id']]
routes = routes[['route_id','route_short_name','route_desc','route_color']]
stop_times = stop_times[['trip_id','stop_id','arrival_time','departure_time']]

In [7]:
stops.head()

stop_id                           stop_name   stop_lat   stop_lon
0  002133  Örs vezér tere M+H, déli tárolótér  47.500366  19.135700
1  002138           Kőbánya alsó vasútállomás  47.483139  19.127891
2  003002             Puskás Ferenc Stadion M  47.500368  19.103406
3  003103    Káposztásmegyer, Mogyoródi-patak  47.598778  19.121447
4  003105             Bécsi út / Vörösvári út  47.548817  19.029722

In [8]:
def check_whether_node_isclose(nodes,new_node):
    threshold_in_meters = 500
    for node in nodes:
        if calculate_distance_between_coordinates_in_meters(new_node[1],new_node[2],node[1],node[2]) < threshold_in_meters:
            return True
    return False

In [9]:
#Joining routes and trips
routes_info = pd.merge(trips, routes, on=['route_id'])
routes_info.head()

route_id    trip_id  direction_id route_short_name  \
0     5200   B1914710             0               M2   
1     5200  B19147100             1               M2   
2     5200  B19147101             0               M2   
3     5200  B19147102             1               M2   
4     5200  B19147103             0               M2   

                               route_desc route_color  
0  Déli pályaudvar M / Örs vezér tere M+H      E41F18  
1  Déli pályaudvar M / Örs vezér tere M+H      E41F18  
2  Déli pályaudvar M / Örs vezér tere M+H      E41F18  
3  Déli pályaudvar M / Örs vezér tere M+H      E41F18  
4  Déli pályaudvar M / Örs vezér tere M+H      E41F18

In [10]:
#Joining stop_times and stops
detailed_stops = pd.merge(stops,stop_times, on=['stop_id'])
detailed_stops.head()

stop_id       stop_name  stop_lat   stop_lon    trip_id arrival_time  \
0  004903  Örs vezér tere  47.50348  19.137211   C2206010     17:12:00   
1  004903  Örs vezér tere  47.50348  19.137211  C22060102     15:42:00   
2  004903  Örs vezér tere  47.50348  19.137211  C22060103     16:00:00   
3  004903  Örs vezér tere  47.50348  19.137211  C22060104     17:42:00   
4  004903  Örs vezér tere  47.50348  19.137211  C22060105     18:00:00   

  departure_time  
0       17:12:00  
1       15:42:00  
2       16:00:00  
3       17:42:00  
4       18:00:00

In [11]:
#Joining all data together
dataset = pd.merge(routes_info,detailed_stops, on=['trip_id'])
dataset.head()

route_id   trip_id  direction_id route_short_name  \
0     5200  B1914710             0               M2   
1     5200  B1914710             0               M2   
2     5200  B1914710             0               M2   
3     5200  B1914710             0               M2   
4     5200  B1914710             0               M2   

                               route_desc route_color stop_id  \
0  Déli pályaudvar M / Örs vezér tere M+H      E41F18  F00063   
1  Déli pályaudvar M / Örs vezér tere M+H      E41F18  F00094   
2  Déli pályaudvar M / Örs vezér tere M+H      E41F18  F00959   
3  Déli pályaudvar M / Örs vezér tere M+H      E41F18  F00961   
4  Déli pályaudvar M / Örs vezér tere M+H      E41F18  F01019   

           stop_name   stop_lat   stop_lon arrival_time departure_time  
0      Batthyány tér  47.506826  19.038103     07:51:37       07:51:37  
1    Déli pályaudvar  47.500450  19.024604     07:48:15       07:48:15  
2  Kossuth Lajos tér  47.505511  19.045769     07:53:00       07:53:00  
3    Deák Ferenc tér  47.497593  19.053857     07:55:00       07:55:00  
4            Astoria  47.494825  19.062457     07:56:35       07:56:35

In [13]:
#Get all unique trips
all_lines = dataset.trip_id.unique()
all_lines.shape

(274452,)

In [14]:
#number of unique routes
all_routes = dataset.route_id.unique()
all_routes.shape

(348,)

In [15]:
# Getting unique trip_ids, randomly from one day. (not the first service by day)
unique_trip_ids = []

#For testing: 
#for route in all_routes[:MAX_ROUTES]: #MAX_ROUTES can be 25-30-50 for better performance
for route in all_routes:
    selected_route_df = (dataset.loc[dataset['route_id'] == str(route)])
    all_trips = selected_route_df.trip_id.unique()
    unique_trip_ids.append(all_trips[0])

In [16]:
def generate_data_for_network(dataframe):
    station_name_labels = {}
    station_name_labels[dataframe['stop_id'][0]] = [dataframe['stop_name'][0]][0]
    station_positions = {}
    lon,lat = extract_coordinates(dataframe['stop_lat'][0],dataframe['stop_lon'][0])
    station_positions[dataframe['stop_id'][0]] = (lon,lat)
    edges = []
    edge_labels = {}
    edge_colors = []
    
    node_labels = {}
    node_labels[dataframe['stop_id'][0]] = {'name': [dataframe['stop_name'][0]][0],'lon': lon,'lat': lat}
    
    for i in range(1,len(dataframe)):
        
        #Getting coordinates
        lon,lat = extract_coordinates(dataframe['stop_lat'][i],dataframe['stop_lon'][i])
        
        station_positions[dataframe['stop_id'][i]] = lon,lat

        #Get current station name
        station_name_labels[dataframe['stop_id'][i]] = [dataframe['stop_name'][i]][0]

        #Getting nodes (departure, arrival)
        departure, arrival = dataframe['stop_id'][i-1], dataframe['stop_id'][i]

        #Calculating time difference, aka weights
        previous_arrival_time, arrival_time = dataframe['arrival_time'][i-1],dataframe['arrival_time'][i]
        time_difference = calculate_time_difference(time1= previous_arrival_time, time2= arrival_time)

        #Adding edges with weights (starting node, ending node, weight)
        edges.append((departure,arrival,time_difference))

        #Adding edge labels
        edge_labels[(departure,arrival)] = [dataframe['route_short_name'][i]][0]

        #Adding edge colors
        edge_colors.append(('#'+[dataframe['route_color'][i]][0]))
        
        node_labels[dataframe['stop_id'][i]] = {'name': [dataframe['stop_name'][i]][0],'lon': lon,'lat': lat}
    
    #Return values: station name labels (node labels), edges, edge labels, edge colors, node positions, node attributes
    return (station_name_labels,edges,edge_labels,edge_colors,station_positions,node_labels)

In [17]:
G = nx.Graph()

#station_name_labels,edges,edge_labels,edge_colors

station_name_labels = {}
station_node_positions = {}
edges = []
edge_labels = {}
edge_colors = []
all_node_attributes = {}

for trip_id in unique_trip_ids:
    trip_data = (dataset.loc[dataset['trip_id'] == trip_id]).sort_values('arrival_time')
    trip_data.reset_index(drop=True, inplace=True)
    
    res = generate_data_for_network(trip_data)
    station_name_labels.update(res[0])
    edges.extend(res[1])
    edge_labels.update(res[2])
    edge_colors.extend(res[3])
    station_node_positions.update(res[4])
    all_node_attributes.update(res[5])


In [18]:
G.add_weighted_edges_from(edges);
nx.set_node_attributes(G, all_node_attributes)

In [19]:
nodekeys = list(G.nodes.keys())

#Getting unique names
names = []
for node_id in nodekeys:
    names.append(G.nodes[node_id]['name'])
names = list(set(names))

nodes_to_merge = []
for unique_stop_name in names:
    multiple_stops_with_same_name = []
    for stop_id, data in G.nodes.items():
        current_name = data['name']
        if current_name == unique_stop_name:
            multiple_stops_with_same_name.append((stop_id,current_name,data['lon'],data['lat']))
    same_named_stops = []
    if len(multiple_stops_with_same_name) == 1: # station is not duplicated
        continue
    for row in multiple_stops_with_same_name:
        if not same_named_stops: #list is empty
            same_named_stops.append([(row[0],row[3],row[2])])
        else:
            could_find_place = False
            current_node = (row[0],row[3],row[2])
            for already_saved_nodes in same_named_stops:
                is_close = check_whether_node_isclose(nodes= already_saved_nodes,new_node= current_node)
                if is_close:
                    already_saved_nodes.append(current_node)
                    could_find_place = True
                    break
            if not could_find_place:
                same_named_stops.append([current_node])
                    
    if len(same_named_stops) > 0:
        nodes_to_merge.append(same_named_stops)

In [20]:
#Merging nodes
for same_name_nodes in nodes_to_merge:
    for same_name in same_name_nodes:
        if len(same_name) > 1:
            base_node_key = same_name[0][0]
            for i in range(1,len(same_name)):
                key = str(same_name[i][0])
                G = nx.contracted_nodes(G, base_node_key, key)

In [45]:
#Removing unused node labels, node positions, edge labels
filtered_labels = {}
filtered_station_node_positions = {}
filtered_edge_labels = {}
for label_key, label in station_name_labels.items():
    if label_key in G.nodes:
        filtered_labels[label_key] = label
        
for pos_key, pos in station_node_positions.items():
    if pos_key in G.nodes:
        filtered_station_node_positions[pos_key] = pos

for k,v in edge_labels.items():
    if k[0] in G.nodes and k[1] in G.nodes:
        filtered_edge_labels[k] = v
        

In [46]:
#Displaying node, saving to PDF
fig = plt.figure(figsize=(140,140))
nx.draw(G,pos=filtered_station_node_positions,labels = filtered_labels,font_size=7, edge_color=edge_colors,node_size=25)
nx.draw_networkx_edge_labels(G,filtered_station_node_positions,edge_labels=filtered_edge_labels,font_size=7,font_color='red')

plt.axis('off')
#plt.show()
plt.savefig('bkk_network.pdf')